# IBM Applied Data Science Capstone – Coursera
Opening a new Coffee shop in New York, USA
New investor is looking to start a new Coffee Shop in New York, USA neighborhoods

.Build a dataframe of neighborhoods of New York, USA by web scraping the data from Wikipedia page
.Get the geographical coordinates of the neighborhoods
.Obtain the venue data for the neighborhoods from Foursquare API
.Explore and cluster the neighborhoods
.Select the best cluster to open a new Coffee Shop


### Introduction
New York City is one of the most famous, romanticized and desired cities for living in the world due to its image portrayed in the pop culture. Some of the worlds' most popular content creators and influencers are located in the city for its stunning backgrounds and instagrammable dining and coffee locations. Combining that with the overall growing trend for coffee and small business coffee shops makes it an attractive investment to open a new coffee shop specifically in NYC where this coffee shop is likely to receive a lot of attention on social media to drive revenue.

Based on the business type and for the sake of this capstone project, our simplified assumptions for the best location would be a high-density population area with a relatively low number of existing coffee shops. Existing competition might in reality be a good factor as a specific neighborhood could be famous for its coffee shops and would attract more customers. In this project, we will examine the landscape of the city on existing competition to identify the best location for the investment.



### Data
Data required to approach the above business case should include New York City neighborhoods' and boroughs' geographical locations (latitude, longitude) and boroughs' population density.

New York City data containing the neighborhoods and boroughs latitudes and longitudes can be obtained from  https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json. While FourSquare API will be used to obtain data on existing coffee shops.



### Methodology
After collecting the data, it will be wrangled into a dataframe format. Using the density data all above average density boroughs will be mapped onto the map. Then using Foursquare we will locate all venues in the following boroughs and then filter by "coffee shop" locations. Finally, the data be will be visually assessed from the resulted map.



### Business Problem
What is the best location(s) for coffee shop in New York City? In what Neighborhood and/or borough is preferred for investing into coffee shop business? What (if any) neighborhood is to go to for a cup of coffee?

### 1. Import libraries

In [8]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors
%matplotlib inline
#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library


print('Libraries imported.')

ModuleNotFoundError: No module named 'folium'

### 2. Scrap data from IBM into a DataFrame

In [37]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')

Data downloaded!


In [38]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [39]:
newyork_data['features'][0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [40]:

columns_name=['Borough', 'Neighborhood', 'Latitude', 'Longitude']
neighborhoods = pd.DataFrame(columns=columns_name)

In [41]:
neighborhoods_data=newyork_data['features']
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [42]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [43]:
print("The dataframe has {} boroughs and {} neighborhoods".format( len(neighborhoods['Borough'].unique()),neighborhoods.shape[0]))

The dataframe has 5 boroughs and 306 neighborhoods


In [44]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [45]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [119]:
CLIENT_ID = 'PNSBWFVXYOJKYJPV1JT3MJMILB3PLRLAMYBSBCRMNWNVNZRH' # your Foursquare ID
CLIENT_SECRET = 'JGJHDJR1UALFBCQOZSFBNVLCEW3ZMDCESRRP4W5ACVHLY1NK' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: PNSBWFVXYOJKYJPV1JT3MJMILB3PLRLAMYBSBCRMNWNVNZRH
CLIENT_SECRET:JGJHDJR1UALFBCQOZSFBNVLCEW3ZMDCESRRP4W5ACVHLY1NK


In [125]:
radius = 5000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [120]:
# neighborhood_latitude=40.87655077879964 
# neighborhood_longitude= -73.91065965862981
# venue_id='55f81cd2498ee903149fcc64'
# LIMIT = 100
# radius = 500
# url = 'https://api.foursquare.com/v2/venues/{}?&client_id={}&client_secret={}&v={}'.format(
#         venue_id,
#         CLIENT_ID, 
#         CLIENT_SECRET, 
#         VERSION)
# requests.get(url).json()["response"]
# lat=40.87655077879964 
# lng= -73.91065965862981
# venue_id='55f81cd2498ee903149fcc64'
# LIMIT = 100
# radius = 500
# url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
#         CLIENT_ID, 
#         CLIENT_SECRET, 
#         VERSION, 
#         lat, 
#         lng, 
#         radius, 
#         LIMIT)
# requests.get(url).json()

{'meta': {'code': 200, 'requestId': '611d61f1f7a6451afa2bc05f'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Marble Hill',
  'headerFullLocation': 'Marble Hill, New York',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 23,
  'suggestedBounds': {'ne': {'lat': 40.88105078329964,
    'lng': -73.90471933917806},
   'sw': {'lat': 40.87205077429964, 'lng': -73.91659997808156}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4baf59e8f964a520a6f93be3',
       'name': 'Bikram Yoga',
       'location': {'address': '5500 Broadway',
        'crossStreet': '230th Street',
        'lat': 40.876843690797934,
        'lng': -73.90620384419528,
        'labeledLatLngs': [{'la

In [228]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'Venue_Name', 'Venue_Latitude', 'Venue_Longitude', 'Venue_Category']

print(venues_df.shape)
venues_df.head()


(30526, 7)


Neighborhood   Latitude  Longitude                   Venue_Name  \
0    Wakefield  40.894705 -73.847201             Lollipops Gelato   
1    Wakefield  40.894705 -73.847201              Ali's Roti Shop   
2    Wakefield  40.894705 -73.847201           Ripe Kitchen & Bar   
3    Wakefield  40.894705 -73.847201     Kingston Tropical Bakery   
4    Wakefield  40.894705 -73.847201  Jackie's West Indian Bakery   

   Venue_Latitude  Venue_Longitude        Venue_Category  
0       40.894123       -73.845892          Dessert Shop  
1       40.894036       -73.856935  Caribbean Restaurant  
2       40.898152       -73.838875  Caribbean Restaurant  
3       40.888568       -73.859885                Bakery  
4       40.889283       -73.843310  Caribbean Restaurant

In [308]:
bb=venues_df[venues_df['Venue_Category']=='Coffee Shop']
cc=bb.groupby(['Neighborhood']).count()
copy=cc.sort_values(ascending=False,by='Venue_Category')
copy

Latitude  Longitude  Venue_Name  Venue_Latitude  \
Neighborhood                                                                 
Ocean Hill                        6          6           6               6   
Sunnyside                         6          6           6               6   
Prince's Bay                      6          6           6               6   
Prospect Lefferts Gardens         6          6           6               6   
Red Hook                          6          6           6               6   
Old Town                          6          6           6               6   
New Lots                          6          6           6               6   
Gowanus                           6          6           6               6   
Country Club                      6          6           6               6   
Bay Terrace                       6          6           6               6   
Hamilton Heights                  6          6           6               6   
Melrose                           6          6           6               6   
Unionport                         5          5           5               5   
Boerum Hill                       5          5           5               5   
Highland Park                     5          5           5               5   
Downtown                          5          5           5               5   
East New York                     5          5           5               5   
Brownsville                       5          5           5               5   
Cypress Hills                     5          5           5               5   
Bushwick                          5          5           5               5   
Pelham Bay                        5          5           5               5   
Castle Hill                       5          5           5               5   
Concourse Village                 5          5           5               5   
Park Slope                        5          5           5               5   
Clason Point                      5          5           5               5   
Far Rockaway                      5          5           5               5   
Sandy Ground                      5          5           5               5   
Woodrow                           5          5           5               5   
Erasmus                           5          5           5               5   
Mariner's Harbor                  5          5           5               5   
Westerleigh                       5          5           5               5   
Graniteville                      5          5           5               5   
Schuylerville                     4          4           4               4   
Stapleton                         4          4           4               4   
East Williamsburg                 4          4           4               4   
Concourse                         4          4           4               4   
Flatlands                         4          4           4               4   
Rugby                             4          4           4               4   
Cobble Hill                       4          4           4               4   
Prospect Heights                  4          4           4               4   
Rosebank                          4          4           4               4   
Prospect Park South               4          4           4               4   
Crown Heights                     4          4           4               4   
Remsen Village                    4          4           4               4   
Emerson Hill                      4          4           4               4   
Egbertville                       4          4           4               4   
Ditmas Park                       4          4           4               4   
St. George                        4          4           4               4   
Great Kills                       4          4           4               4   
High  Bridge                      4          4   

In [310]:
copy.groupby(["Neighborhood"]).count()


Latitude  Longitude  Venue_Name  Venue_Latitude  \
Neighborhood                                                                 
Allerton                          1          1           1               1   
Annadale                          1          1           1               1   
Arden Heights                     1          1           1               1   
Arlington                         1          1           1               1   
Arrochar                          1          1           1               1   
Arverne                           1          1           1               1   
Astoria                           1          1           1               1   
Astoria Heights                   1          1           1               1   
Auburndale                        1          1           1               1   
Battery Park City                 1          1           1               1   
Bay Ridge                         1          1           1               1   
Bay Terrace                       1          1           1               1   
Baychester                        1          1           1               1   
Bayside                           1          1           1               1   
Bayswater                         1          1           1               1   
Bedford Park                      1          1           1               1   
Bedford Stuyvesant                1          1           1               1   
Beechhurst                        1          1           1               1   
Bellaire                          1          1           1               1   
Belle Harbor                      1          1           1               1   
Bellerose                         1          1           1               1   
Belmont                           1          1           1               1   
Bensonhurst                       1          1           1               1   
Bergen Beach                      1          1           1               1   
Blissville                        1          1           1               1   
Bloomfield                        1          1           1               1   
Boerum Hill                       1          1           1               1   
Borough Park                      1          1           1               1   
Breezy Point                      1          1           1               1   
Briarwood                         1          1           1               1   
Brighton Beach                    1          1           1               1   
Broad Channel                     1          1           1               1   
Broadway Junction                 1          1           1               1   
Bronxdale                         1          1           1               1   
Brooklyn Heights                  1          1           1               1   
Brookville                        1          1           1               1   
Brownsville                       1          1           1               1   
Bulls Head                        1          1           1               1   
Bushwick                          1          1           1               1   
Butler Manor                      1          1           1               1   
Canarsie                          1          1           1               1   
Carnegie Hill                     1          1           1               1   
Carroll Gardens                   1          1           1               1   
Castle Hill                       1          1           1               1   
Castleton Corners                 1          1           1               1   
Central Harlem                    1          1           1               1   
Charleston                        1          1           1               1   
Chelsea                           1          1           1               1   
Chinatown                         1          1           1               1   
City Island                       1          1   

In [231]:

print('There are {} uniques categories.'.format(len(venues_df['Venue_Category'].unique())))

There are 349 uniques categories.


In [232]:
venues_df['Venue_Category'].unique()[:50]

array(['Dessert Shop', 'Caribbean Restaurant', 'Bakery', 'Pub', 'Bar',
       'Pizza Place', 'Pharmacy', 'Trail', 'Café', 'Grocery Store', 'Gym',
       'Bagel Shop', 'Brewery', 'Fast Food Restaurant', 'Ice Cream Shop',
       'Kitchen Supply Store', 'Seafood Restaurant', 'Wine Shop', 'Diner',
       'Brazilian Restaurant', 'Italian Restaurant', 'Pet Store',
       'American Restaurant', 'Asian Restaurant',
       'Furniture / Home Store', 'Sports Bar', 'Burger Joint', 'Park',
       'Deli / Bodega', 'Donut Shop', 'Mexican Restaurant', 'Coffee Shop',
       'Electronics Store', 'Cajun / Creole Restaurant',
       'Botanical Garden', 'Supermarket', 'Spanish Restaurant',
       'Japanese Restaurant', 'Garden', 'Track', 'Breakfast Spot',
       'Frozen Yogurt Shop', 'Video Game Store', 'Beer Bar', 'Exhibit',
       'Vineyard', 'Gift Shop', 'Stables', 'Cosmetics Shop',
       'Shopping Mall'], dtype=object)

In [233]:

# one hot encoding
nyc_onehot = pd.get_dummies(venues_df[['Venue_Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
nyc_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [nyc_onehot.columns[-1]] + list(nyc_onehot.columns[:-1])
nyc_onehot = nyc_onehot[fixed_columns]

print(nyc_onehot.shape)
nyc_onehot.head(10)

(30526, 350)


Neighborhoods  Accessories Store  African Restaurant  Airport Food Court  \
0     Wakefield                  0                   0                   0   
1     Wakefield                  0                   0                   0   
2     Wakefield                  0                   0                   0   
3     Wakefield                  0                   0                   0   
4     Wakefield                  0                   0                   0   
5     Wakefield                  0                   0                   0   
6     Wakefield                  0                   0                   0   
7     Wakefield                  0                   0                   0   
8     Wakefield                  0                   0                   0   
9     Wakefield                  0                   0                   0   

   Airport Lounge  Airport Service  American Restaurant  Amphitheater  \
0               0                0                    0             0   
1               0                0                    0             0   
2               0                0                    0             0   
3               0                0                    0             0   
4               0                0                    0             0   
5               0                0                    0             0   
6               0                0                    0             0   
7               0                0                    0             0   
8               0                0                    0             0   
9               0                0                    0             0   

   Animal Shelter  Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0               0         0       0                 0                       0   
1               0         0       0                 0                       0   
2               0         0       0                 0                       0   
3               0         0       0                 0                       0   
4               0         0       0                 0                       0   
5               0         0       0                 0                       0   
6               0         0       0                 0                       0   
7               0         0       0                 0                       0   
8               0         0       0                 0                       0   
9               0         0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0            0           0                    0                 0   
1            0           0                    0                 0   
2            0           0                    0                 0   
3            0           0                    0                 0   
4            0           0                    0                 0   
5            0           0                    0                 0   
6            0           0                    0                 0   
7            0           0                    0                 0   
8            0           0                    0                 0   
9            0           0                    0                 0   

   Athletics & Sports  Austrian Restaurant  Automotive Shop  BBQ Joint  \
0                   0                    0                0          0   
1                   0                    0                0          0   
2                   0                    0                0          0   
3                   0                    0                0          0   
4                   0                    0                0          0   
5                   0                    0                0          0   
6                   0                    0                0          0   
7                   0                    0                0          0   
8                   0

In [234]:
nyc_grouped = nyc_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(nyc_grouped.shape)
nyc_grouped

(302, 350)


Neighborhoods  Accessories Store  African Restaurant  \
0                     Allerton               0.00                0.00   
1                     Annadale               0.00                0.00   
2                Arden Heights               0.00                0.00   
3                    Arlington               0.01                0.00   
4                     Arrochar               0.00                0.00   
5                      Arverne               0.00                0.00   
6                      Astoria               0.00                0.00   
7              Astoria Heights               0.00                0.00   
8                   Auburndale               0.00                0.00   
9                   Bath Beach               0.00                0.00   
10           Battery Park City               0.00                0.00   
11                   Bay Ridge               0.00                0.00   
12                 Bay Terrace               0.00                0.00   
13                  Baychester               0.00                0.00   
14                     Bayside               0.00                0.00   
15                   Bayswater               0.00                0.00   
16                Bedford Park               0.00                0.00   
17          Bedford Stuyvesant               0.00                0.00   
18                  Beechhurst               0.00                0.00   
19                    Bellaire               0.00                0.00   
20                Belle Harbor               0.00                0.00   
21                   Bellerose               0.00                0.00   
22                     Belmont               0.00                0.00   
23                 Bensonhurst               0.00                0.00   
24                Bergen Beach               0.00                0.00   
25                  Blissville               0.00                0.00   
26                  Bloomfield               0.00                0.00   
27                 Boerum Hill               0.00                0.00   
28                Borough Park               0.00                0.00   
29                Breezy Point               0.00                0.00   
30                   Briarwood               0.00                0.00   
31              Brighton Beach               0.00                0.00   
32               Broad Channel               0.01                0.00   
33           Broadway Junction               0.00                0.00   
34                   Bronxdale               0.00                0.00   
35            Brooklyn Heights               0.00                0.00   
36                  Brookville               0.00                0.00   
37                 Brownsville               0.00                0.01   
38                  Bulls Head               0.00                0.00   
39                    Bushwick               0.00                0.00   
40                Butler Manor               0.00                0.00   
41             Cambria Heights               0.00                0.00   
42                    Canarsie               0.00                0.00   
43               Carnegie Hill               0.00                0.00   
44             Carroll Gardens               0.00                0.00   
45                 Castle Hill               0.00                0.00   
46           Castleton Corners               0.00                0.00   
47              Central Harlem               0.00                0.00   
48                  Charleston               0.00                0.00   
49                     Chelsea               0.00                0.00   
50                   Chinatown               0.00                0.00   
51                 City Island               0.00                0.00   
52                   City Line               0.00                0.00   
53                Civic Center               0.00                0.00   
54

In [235]:

len(nyc_grouped[nyc_grouped["Coffee Shop"] > 0])

272

In [236]:
nyc_coffeeshop = nyc_grouped[["Neighborhoods","Coffee Shop"]]
nyc_coffeeshop.head()

Neighborhoods  Coffee Shop
0       Allerton     0.030000
1       Annadale     0.010101
2  Arden Heights     0.010000
3      Arlington     0.030000
4       Arrochar     0.020000

In [237]:
nyc_coffeeshop=nyc_coffeeshop.sort_values(ascending=False,by='Coffee Shop')
nyc_coffeeshop.head()

Neighborhoods  Coffee Shop
200        Ocean Hill         0.06
202          Old Town         0.06
124  Hamilton Heights         0.06
191          New Lots         0.06
217      Prince's Bay         0.06

### Cluster Neighborhoods
Run k-means to cluster the neighborhoods in NYC into 3 clusters.

In [238]:

# set number of clusters
kclusters = 3

nyc_clustering = nyc_coffeeshop.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(nyc_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:30]

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [239]:
# Create a new dataframe that includes the cluster label
nyc_merged = nyc_coffeeshop.copy()

# add clustering labels
nyc_merged["Cluster Labels"] = kmeans.labels_


nyc_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
nyc_merged.head(10)

Neighborhood  Coffee Shop  Cluster Labels
200                 Ocean Hill         0.06               1
202                   Old Town         0.06               1
124           Hamilton Heights         0.06               1
191                   New Lots         0.06               1
217               Prince's Bay         0.06               1
113                    Gowanus         0.06               1
171                    Melrose         0.06               1
226                   Red Hook         0.06               1
219  Prospect Lefferts Gardens         0.06               1
67                Country Club         0.06               1

In [241]:
# nyc_merged = nyc_merged.join(neighborhoods.set_index("Neighborhood"), on="Neighborhood")

print(nyc_merged.shape)
nyc_merged # check the last columns!

(306, 6)


Neighborhood  Coffee Shop  Cluster Labels        Borough  \
200                 Ocean Hill     0.060000               1       Brooklyn   
202                   Old Town     0.060000               1  Staten Island   
124           Hamilton Heights     0.060000               1      Manhattan   
191                   New Lots     0.060000               1       Brooklyn   
217               Prince's Bay     0.060000               1  Staten Island   
113                    Gowanus     0.060000               1       Brooklyn   
171                    Melrose     0.060000               1          Bronx   
226                   Red Hook     0.060000               1       Brooklyn   
219  Prospect Lefferts Gardens     0.060000               1       Brooklyn   
67                Country Club     0.060000               1          Bronx   
73                    Downtown     0.050000               1       Brooklyn   
276                  Unionport     0.050000               1          Bronx   
69               Cypress Hills     0.050000               1       Brooklyn   
79               East New York     0.050000               1       Brooklyn   
209                 Pelham Bay     0.050000               1          Bronx   
39                    Bushwick     0.050000               1       Brooklyn   
37                 Brownsville     0.050000               1       Brooklyn   
92                     Erasmus     0.050000               1       Brooklyn   
93                Far Rockaway     0.050000               1         Queens   
64           Concourse Village     0.050000               1          Bronx   
290                Westerleigh     0.050000               1  Staten Island   
55                Clason Point     0.050000               1          Bronx   
27                 Boerum Hill     0.050000               1       Brooklyn   
45                 Castle Hill     0.050000               1          Bronx   
207                 Park Slope     0.050000               1       Brooklyn   
299                    Woodrow     0.050000               1  Staten Island   
243               Sandy Ground     0.050000               1  Staten Island   
169           Mariner's Harbor     0.050000               1  Staten Island   
128              Highland Park     0.050000               1       Brooklyn   
115               Graniteville     0.050000               1  Staten Island   
242                      Rugby     0.040000               1       Brooklyn   
156                Little Neck     0.040000               1         Queens   
68               Crown Heights     0.040000               1       Brooklyn   
82           East Williamsburg     0.040000               1       Brooklyn   
70                 Ditmas Park     0.040000               1       Brooklyn   
161                      Malba     0.040000               1         Queens   
244              Schuylerville     0.040000               1          Bronx   
152            Lighthouse Hill     0.040000               1  Staten Island   
63                   Concourse     0.040000               1          Bronx   
172             Middle Village     0.040000               1         Queens   
251                  Soundview     0.040000               1          Bronx   
230              Richmond Town     0.040000               1  Staten Island   
87                 Egbertville     0.040000               1  Staten Island   
199                    Oakwood     0.040000               1  Staten Island   
88                    Elm Park     0.040000               1  Staten Island   
138                Hunts Point     0.040000               1          Bronx   
91                Emerson Hill     0.040000               1  Staten Island   
259                 St. George     0.040000               1  Staten Island   
260                  Stapleton     0.040000               1  Staten Island   
270              Tompkinsville     0.040000               1  Staten Island   
98                   Flatlands     0.040

In [242]:

# Sort the results by Cluster Labels
print(nyc_merged.shape)
nyc_merged.sort_values(["Cluster Labels"], inplace=True)
nyc_merged

(306, 6)


Neighborhood  Coffee Shop  Cluster Labels        Borough  \
151                 Lenox Hill     0.000000               0      Manhattan   
137              Hunters Point     0.010000               0         Queens   
30                   Briarwood     0.010000               0         Queens   
133               Howard Beach     0.010000               0         Queens   
31              Brighton Beach     0.010000               0       Brooklyn   
131                 Holliswood     0.010000               0         Queens   
130                     Hollis     0.010000               0         Queens   
129                  Hillcrest     0.010000               0         Queens   
53                Civic Center     0.010000               0      Manhattan   
222            Queensboro Hill     0.010000               0         Queens   
42                    Canarsie     0.010000               0       Brooklyn   
110            Gerritsen Beach     0.010000               0       Brooklyn   
108               Fulton Ferry     0.010000               0       Brooklyn   
49                     Chelsea     0.010000               0      Manhattan   
49                     Chelsea     0.010000               0  Staten Island   
102               Forest Hills     0.010000               0         Queens   
50                   Chinatown     0.010000               0      Manhattan   
95          Financial District     0.010000               0      Manhattan   
89                    Elmhurst     0.010000               0         Queens   
145                Kew Gardens     0.010000               0         Queens   
149                  Laurelton     0.010000               0         Queens   
26                  Bloomfield     0.010000               0  Staten Island   
29                Breezy Point     0.010000               0         Queens   
24                Bergen Beach     0.010000               0       Brooklyn   
141             Jamaica Center     0.010000               0         Queens   
143              Jamaica Hills     0.010000               0         Queens   
1                     Annadale     0.010101               0  Staten Island   
292             Williamsbridge     0.010000               0          Bronx   
300                   Woodside     0.010000               0         Queens   
283                  Wakefield     0.010000               0          Bronx   
229              Richmond Hill     0.010000               0         Queens   
280                     Utopia     0.010000               0         Queens   
279            Upper West Side     0.010000               0      Manhattan   
278            Upper East Side     0.010000               0      Manhattan   
273                    Tribeca     0.010000               0      Manhattan   
227                  Rego Park     0.010000               0         Queens   
265          Sunnyside Gardens     0.010000               0         Queens   
263            Stuyvesant Town     0.010000               0      Manhattan   
258                 St. Albans     0.010000               0         Queens   
234                   Rochdale     0.010000               0         Queens   
256        Springfield Gardens     0.010000               0         Queens   
249                       Soho     0.010000               0      Manhattan   
246             Sheepshead Bay     0.010000               0       Brooklyn   
225                 Ravenswood     0.010000               0         Queens   
301                  Yorkville     0.010000               0      Manhattan   
142            Jamaica Estates     0.010000               0         Queens   
81                East Village     0.010000               0      Manhattan   
66                      Corona     0.010000               0         Queens   
213                    Pomonok     0.010000               0         Queens   
198            Oakland Gardens     0.010000               0         Queens   
2                Arden Heights     0.010

In [243]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(nyc_merged['Latitude'], nyc_merged['Longitude'], nyc_merged['Neighborhood'], nyc_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [7]:
map_clusters.save('NYC_neighborhood_map_clusters.html')

NameError: name 'map_clusters' is not defined

### Examine Clusters

In [6]:
k_0=nyc_merged.loc[nyc_merged['Cluster Labels'] == 0].reset_index()
k_0

NameError: name 'nyc_merged' is not defined

In [246]:
k_1=nyc_merged.loc[nyc_merged['Cluster Labels'] == 1]
k_1

Neighborhood  Coffee Shop  Cluster Labels        Borough  \
200                 Ocean Hill         0.06               1       Brooklyn   
98                   Flatlands         0.04               1       Brooklyn   
266                Sunset Park         0.04               1       Brooklyn   
60                 Cobble Hill         0.04               1       Brooklyn   
181                Morris Park         0.04               1          Bronx   
127               High  Bridge         0.04               1          Bronx   
228             Remsen Village         0.04               1       Brooklyn   
270              Tompkinsville         0.04               1  Staten Island   
260                  Stapleton         0.04               1  Staten Island   
259                 St. George         0.04               1  Staten Island   
91                Emerson Hill         0.04               1  Staten Island   
138                Hunts Point         0.04               1          Bronx   
88                    Elm Park         0.04               1  Staten Island   
87                 Egbertville         0.04               1  Staten Island   
230              Richmond Town         0.04               1  Staten Island   
251                  Soundview         0.04               1          Bronx   
172             Middle Village         0.04               1         Queens   
119                Great Kills         0.04               1  Staten Island   
63                   Concourse         0.04               1          Bronx   
104                Fort Greene         0.04               1       Brooklyn   
28                Borough Park         0.04               1       Brooklyn   
294                Willowbrook         0.04               1  Staten Island   
220        Prospect Park South         0.04               1       Brooklyn   
25                  Blissville         0.04               1         Queens   
208                Parkchester         0.04               1          Bronx   
218           Prospect Heights         0.04               1       Brooklyn   
40                Butler Manor         0.04               1  Staten Island   
289         Westchester Square         0.04               1          Bronx   
287                 West Farms         0.04               1          Bronx   
33           Broadway Junction         0.04               1       Brooklyn   
46           Castleton Corners         0.04               1  Staten Island   
216              Port Richmond         0.04               1  Staten Island   
212            Pleasant Plains         0.04               1  Staten Island   
295            Windsor Terrace         0.04               1       Brooklyn   
18                  Beechhurst         0.04               1         Queens   
285                 Weeksville         0.04               1       Brooklyn   
238                   Rosebank         0.04               1  Staten Island   
152            Lighthouse Hill         0.04               1  Staten Island   
199                    Oakwood         0.04               1  Staten Island   
161                      Malba         0.04               1         Queens   
37                 Brownsville         0.05               1       Brooklyn   
39                    Bushwick         0.05               1       Brooklyn   
209                 Pelham Bay         0.05               1          Bronx   
244              Schuylerville         0.04               1          Bronx   
69               Cypress Hills         0.05               1       Brooklyn   
276                  Unionport         0.05               1          Bronx   
73                    Downtown         0.05               1       Brooklyn   
92                     Erasmus         0.05               1       Brooklyn   
67                Country Club         0.06               1          Bronx   
226                   Red Hook         0.06               1       Brooklyn   
171                    Melrose         0

In [247]:
k_2=nyc_merged.loc[nyc_merged['Cluster Labels'] == 2]
k_2

Neighborhood  Coffee Shop  Cluster Labels        Borough  \
16           Bedford Park     0.030000               2          Bronx   
11              Bay Ridge     0.030000               2       Brooklyn   
165        Manhattanville     0.030000               2      Manhattan   
3               Arlington     0.030000               2  Staten Island   
158              Longwood     0.030000               2          Bronx   
248           Silver Lake     0.030000               2  Staten Island   
166         Manor Heights     0.030000               2  Staten Island   
247           Shore Acres     0.030000               2  Staten Island   
296               Wingate     0.030000               2       Brooklyn   
59             Co-op City     0.030000               2          Bronx   
120            Greenpoint     0.020000               2       Brooklyn   
8              Auburndale     0.030000               2         Queens   
232             Ridgewood     0.030000               2         Queens   
235        Rockaway Beach     0.030000               2         Queens   
58           Clinton Hill     0.030000               2       Brooklyn   
231       Richmond Valley     0.030000               2  Staten Island   
264             Sunnyside     0.030000               2  Staten Island   
264             Sunnyside     0.030000               2         Queens   
123           Grymes Hill     0.030000               2  Staten Island   
116            Grant City     0.030000               2  Staten Island   
261         Starrett City     0.030000               2       Brooklyn   
183            Mott Haven     0.030000               2          Bronx   
22                Belmont     0.030000               2          Bronx   
5                 Arverne     0.031915               2         Queens   
125               Hammels     0.033333               2         Queens   
121            Greenridge     0.020000               2  Staten Island   
17     Bedford Stuyvesant     0.030000               2       Brooklyn   
12            Bay Terrace     0.030000               2  Staten Island   
126     Heartland Village     0.020000               2  Staten Island   
257        Spuyten Duyvil     0.020000               2          Bronx   
35       Brooklyn Heights     0.030000               2       Brooklyn   
210        Pelham Gardens     0.030000               2          Bronx   
206             Park Hill     0.030000               2  Staten Island   
34              Bronxdale     0.030000               2          Bronx   
96               Flatbush     0.030000               2       Brooklyn   
56                Clifton     0.030000               2  Staten Island   
269             Todt Hill     0.030000               2  Staten Island   
99            Floral Park     0.030000               2         Queens   
32          Broad Channel     0.030000               2         Queens   
62                Concord     0.030000               2  Staten Island   
190        New Dorp Beach     0.030000               2  Staten Island   
291            Whitestone     0.030000               2         Queens   
105         Fort Hamilton     0.030000               2       Brooklyn   
281              Van Nest     0.030000               2          Bronx   
106             Fox Hills     0.030000               2  Staten Island   
44        Carroll Gardens     0.030000               2       Brooklyn   
90            Eltingville     0.023529               2  Staten Island   
136              Huguenot     0.021978               2  Staten Island   
201         Ocean Parkway     0.020000               2       Brooklyn   
196            North Side     0.020000               2       Brooklyn   
221        Queens Village     0.020000               2         Queens   
38             Bulls Head     0.030000               2  Staten Island   
51            City Island     0.030000               2          Bronx   
86         Edgewater Park     0.030000               2          Bronx  

In [5]:
len_cluster_0 = len(k_0)
len_cluster_0 = len(k_1)
len_cluster_0 = len(k_2)

print('Total neighborhoods in cluster 0 =', len_cluster_0)
print('Total neighborhoods in cluster 1 =', len_cluster_1)
print('Total neighborhoods in cluster 2 =', len_cluster_2)

NameError: name 'k_0' is not defined

# Conclusion

#### Cluster 0: means that the neighborhoods that have 1 Coffee Shop , around 32%


#### Cluster 1: means that the neighborhoods that have 4 or 5 or 6 Coffee Shops , around 24.5%


#### Cluster 2: means that the neighborhoods that have 2 or 3 Coffee Shops , around 43%

This is showing that new Coffee Shops can be opened in neighborhoods listed in cluster 1 as less competition compared to cluster 0 and 2. Meanwhile, Coffee Shops in cluster 1 are likely suffering from intense competition due to oversupply because cluster 1 is the neighborhoods that have 4,5 or 6 coffee shops. So we can figure out which boroughs have more coffee shops.

### Now we group them by neighborhood to understand which neighborhoods have more coffee shops

In [251]:
print(k_0.groupby(k_0['Borough']).count()['Coffee Shop'])
print(k_1.groupby(k_1['Borough']).count()['Coffee Shop'])
print(k_2.groupby(k_2['Borough']).count()['Coffee Shop'])



Borough
Bronx             7
Brooklyn         15
Manhattan        32
Queens           42
Staten Island     4
Name: Coffee Shop, dtype: int64
Borough
Bronx            16
Brooklyn         29
Manhattan         1
Queens            6
Staten Island    23
Name: Coffee Shop, dtype: int64
Borough
Bronx            29
Brooklyn         26
Manhattan         7
Queens           33
Staten Island    36
Name: Coffee Shop, dtype: int64


So, we concentrate on cluster 1. we know that the Brooklyn and Manhattan are crowded and their density of population are high. So, we can choose these 2 boroughs but as you can see from above, Brooklyn has many coffee shops on 29 neighborhoods so we rather to choose Manhattan because it has 6 coffee shops on just 1 neighborhood(Hamilton Heights) and the other neighborhoods are on cluster 0 or 2.Thus, we choose other neighborhoods except Hamilton Heights.

In [255]:
print(k_1[k_1['Borough']=='Manhattan'])
# print(k_1[k_1['Borough']=='Brooklyn'])

         Neighborhood  Coffee Shop  Cluster Labels    Borough   Latitude  \
124  Hamilton Heights         0.06               1  Manhattan  40.823604   

     Longitude  
124 -73.949688  


Eliminate 'Hamilton Heights'

In [264]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_boroughs=manhattan_data[(manhattan_data['Neighborhood']!='Hamilton Heights')]
manhattan_boroughs['Neighborhood']

0             Marble Hill
1               Chinatown
2      Washington Heights
3                  Inwood
5          Manhattanville
6          Central Harlem
7             East Harlem
8         Upper East Side
9               Yorkville
10             Lenox Hill
11       Roosevelt Island
12        Upper West Side
13         Lincoln Square
14                Clinton
15                Midtown
16            Murray Hill
17                Chelsea
18      Greenwich Village
19           East Village
20        Lower East Side
21                Tribeca
22           Little Italy
23                   Soho
24           West Village
25       Manhattan Valley
26    Morningside Heights
27               Gramercy
28      Battery Park City
29     Financial District
30          Carnegie Hill
31                   Noho
32           Civic Center
33          Midtown South
34           Sutton Place
35             Turtle Bay
36             Tudor City
37        Stuyvesant Town
38               Flatiron
39          

### For having accurate neighborhoods and less competition we can eliminate the neighborhoods that are on cluster 2(3 or 2 coffee shops on each neighborhood).

In [4]:
print(k_2[k_2['Borough']=='Manhattan'])


NameError: name 'k_2' is not defined

In [3]:
# manhattan_places_for_coffee_shops=manhattan_data[(manhattan_data['Neighborhood']!='Manhattanville')&(manhattan_data['Neighborhood']!='Washington Heights')&(manhattan_data['Neighborhood']!='Inwood')&(manhattan_data['Neighborhood']!='Central Harlem')&(manhattan_data['Neighborhood']!='Carnegie Hill')&(manhattan_data['Neighborhood']!='Marble Hill')&(manhattan_data['Neighborhood']!='Morningside Heights')]

# mm=manhattan_places_for_coffee_shops[['Borough','Neighborhood']]
# copy=copy.reset_index()
# copy['Neighborhood']
vv = mm.join(copy.set_index("Neighborhood"), on="Neighborhood")
vv[['Borough','Neighborhood','Venue_Category']]

NameError: name 'mm' is not defined